# Analyse de l’épidémie de choléra à Soho (1854) — Reproduction de la carte de John Snow - Victor GERENTON

Ce notebook a pour objectif de reproduire la célèbre carte de John Snow montrant la répartition des décès dus au choléra à Soho en 1854. À l'aide de données géographiques historiques et d'outils modernes de visualisation, nous allons :

1. Visualiser les lieux de décès et les pompes à eau sur une carte interactive.
2. Explorer des méthodes d'analyse spatiale pour mettre en évidence le rôle central de la pompe de Broad Street.



## Installation des biliothèques

L'ensembles des biliothèques et leur version respective se trouvent dans le fichier 'requirements.txt'

In [ ]:
!pip install -r requirements.txt

print(("----------------------------------------"))
print("Toutes les bibliothèques sont installées !")

## Importation des biliothèques

In [ ]:
# Importation des bibliothèques nécessaires à notre analyse
import geopandas as gpd
import folium
import matplotlib.pyplot as plt
from shapely.geometry import Point

print("Toutes les bibliothèques sont importées !")

## Étape 1 — Chargement des données

Nous utilisons ici les fichiers Shapefile fournis dans l’archive `SnowGIS_SHP` provenant de ce site :

https://blog.rtwilson.com/john-snows-cholera-data-in-more-formats/


Ces fichiers contiennent les données géographiques suivantes :

- `Cholera_Deaths.shp` : emplacements des décès dus au choléra, avec le nombre de morts par adresse.
- `Pumps.shp` : emplacements des pompes à eau publiques dans le quartier de Soho.

Nous utilisons la bibliothèque `GeoPandas` pour lire ces fichiers et vérifier que les données sont bien chargées avec le bon système de coordonnées.


In [9]:
# Chargement des shapefiles avec GeoPandas
deaths = gpd.read_file("data/Cholera_Deaths.shp")
pumps = gpd.read_file("data/Pumps.shp")

# Aperçu des données
display(deaths.head())
display(pumps.head())

# Vérification du système de coordonnées (CRS)
print("CRS des décès :", deaths.crs)
print("CRS des pompes :", pumps.crs)


Id  Count                       geometry
0   0      3  POINT (529308.741 181031.352)
1   0      2  POINT (529312.164 181025.172)
2   0      1  POINT (529314.382 181020.294)
3   0      1  POINT (529317.380 181014.259)
4   0      4  POINT (529320.675 181007.872)

Id                       geometry
0   0  POINT (529396.539 181025.063)
1   0  POINT (529192.538 181079.391)
2   0  POINT (529183.740 181193.735)
3   0  POINT (529748.911 180924.207)
4   0  POINT (529613.205 180896.804)

CRS des décès : epsg:27700
CRS des pompes : epsg:27700


## Étape 2 — Conversion des coordonnées pour Folium

Folium utilise sur le système de coordonnées **WGS 84** (latitude/longitude), qui est utilisé par défaut dans les cartes web comme OpenStreetMap.  
Cependant, nos fichiers shapefile utilisent actuellement le système **British National Grid** (EPSG:27700), qui fonctionne avec des coordonnées en mètres, propres au Royaume-Uni.

Afin de pouvoir afficher correctement nos données sur une carte interactive avec Folium, il est nécessaire de les convertir vers le système de projection WGS 84 (**EPSG:4326**).  
Cette opération est appelée une **reprojection**. Elle permet à nos points d'apparaître au bon endroit sur la carte.

Nous réalisons cette conversion avec la méthode .to_crs(epsg=4326) de GeoPandas, qui transforme les coordonnées de chaque géométrie.

In [10]:
# Reprojection en EPSG:4326 (latitude/longitude)
deaths_wgs84 = deaths.to_crs(epsg=4326)
pumps_wgs84 = pumps.to_crs(epsg=4326)

# Aperçu pour vérification
deaths_wgs84.head()


Id  Count                   geometry
0   0      3  POINT (-0.13793 51.51342)
1   0      2  POINT (-0.13788 51.51336)
2   0      1  POINT (-0.13785 51.51332)
3   0      1  POINT (-0.13781 51.51326)
4   0      4  POINT (-0.13777 51.51320)

## Étape 3 — Création de la carte interactive

Nous utilisons la bibliothèque `folium` pour créer une carte interactive centrée sur le quartier de Soho.

- Les **cercles rouges** représentent les décès dus au choléra. Leur taille est proportionnelle au nombre de morts enregistrés à cette adresse (`Count`).
- Les **marqueurs bleus** représentent les pompes à eau publiques.

Cette visualisation permet de retrouver la logique de la carte originale de John Snow, en montrant la concentration des décès autour de certaines pompes.


In [11]:
# Obtenir le centre de la carte en prenant le centre des décès
map_center = [deaths_wgs84.geometry.y.mean(), deaths_wgs84.geometry.x.mean()]

# Créer la carte Folium centrée sur Soho
m = folium.Map(location=map_center, zoom_start=17, tiles='cartodbpositron')

# Ajouter les décès avec des cercles proportionnels à Count
for _, row in deaths_wgs84.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=row['Count'] * 1.5,  # multiplier pour avoir une taille visible
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.6,
        popup=f"{row['Count']} décès"
    ).add_to(m)

# Ajouter les pompes avec une icône bleue
for _, row in pumps_wgs84.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        icon=folium.Icon(color='blue', icon='tint', prefix='fa'),
        popup="Pompe à eau"
    ).add_to(m)

# Afficher la carte
m


## Étape 4 — Visualisation de la densité des décès avec une Heatmap

Pour identifier visuellement les zones les plus touchées par l’épidémie, nous utilisons une **carte de chaleur** (heatmap).  
Chaque point de décès est pondéré par le nombre de morts (`Count`). On observe ainsi une zone de concentration très nette autour d'une certaine pompe.
On voyait déjà cela avec les cercles mais je trouve la heat map plus parlante.


In [12]:
from folium.plugins import HeatMap

# Extraire les points avec leur pondération
heat_data = [[row.geometry.y, row.geometry.x, row['Count']] for _, row in deaths_wgs84.iterrows()]

# Nouvelle carte centrée sur Soho
m_heat = folium.Map(location=map_center, zoom_start=17, tiles='cartodbpositron')

# Ajouter la heatmap des décès
HeatMap(heat_data, radius=15, blur=10, max_zoom=18).add_to(m_heat)

# Ajouter les pompes pour référence
for _, row in pumps_wgs84.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        icon=folium.Icon(color='blue', icon='tint', prefix='fa'),
        popup="Pompe à eau"
    ).add_to(m_heat)

# Afficher la heatmap
m_heat


## Conclusion

Grâce à nos outils de visualisation de données géospatiales, nous avons pu reproduire et enrichir l’analyse historique de John Snow sur l’épidémie de choléra de 1854 à Soho.

- Nous avons visualisé les lieux de décès avec des cercles proportionnels au nombre de morts.
- Nous avons localisé les pompes à eau sur la même carte.
- La carte de chaleur a clairement mis en évidence une forte concentration de décès autour d'une pompe spécifique, celle de Broad Street.


Victor Gérenton
---
